In [1]:
#Use with python/3.6.0 and tensorflow/1.10

import math
import sys
from sklearn.linear_model import LogisticRegression
import random
import os
import csv
import json
from collections import defaultdict
import gensim
import numpy as np
import pandas as pd
import sklearn.metrics as metrics

from sklearn.metrics import f1_score

from sklearn.linear_model import LogisticRegressionCV
import sklearn.metrics as metrics
from sklearn import metrics
from sklearn.utils import resample
from sklearn.model_selection import GridSearchCV
from glove import Corpus, Glove
from bert_serving.client import BertClient
bc = BertClient()
import os
import tensorflow as tf
import numpy as np
import scipy.spatial.distance as ds
from bilm import Batcher, BidirectionalLanguageModel, weight_layers
 


from tensorflow.python.keras.models import Sequential
from tensorflow.python.keras.layers import Dense, Dropout

from tensorflow.python.keras.wrappers.scikit_learn import KerasRegressor

from sklearn.model_selection import GridSearchCV, KFold

from sklearn.metrics import accuracy_score
from tensorflow.python.keras.constraints import maxnorm
from tensorflow.python.keras.callbacks import EarlyStopping
from sklearn.metrics import make_scorer, r2_score, mean_absolute_error, mean_squared_error

lib_path = os.path.abspath(os.path.join('..', 'lib'))
sys.path.append(lib_path)

ds = "mimic"
data_path = "/Users/emily/Documents/mimic_seq/"
#data_path = '/home/egetzen/jill_mimic_seq'
window=10
size=100
decay=5
skipgram=1
norm=False
random.seed(1)

# list for files
train_files = []
valid_files = []
full_data_files = []

In [2]:
for i in range(7):
    train_files.append(data_path + 'test_'+str(i))
for i in range(7,10):
    valid_files.append(data_path + 'test_'+str(i))
for i in range(10):
    full_data_files.append(data_path + 'test_'+str(i))


In [3]:
diag_totals = defaultdict(lambda: 0)
diag_totals2 = defaultdict(lambda: 0)
diag_joined = defaultdict(lambda: 0)
diag_joined2 = defaultdict(lambda:0)
test = defaultdict(lambda:0)
sentences = []
final_dx_train = []
disease_prev = []
list_duplicates = []
diag = []


In [4]:
# Location of pretrained LM.  Here we use the test fixtures.
datadir = '/users/emily/Documents/swp'
vocab_file = '/users/emily/Documents/swp/vocab.txt'
options_file = '/users/emily/Documents/swp/checkpoint/options.json'
weight_file = '/users/emily/Documents/swp/swp_weights.hdf5'
#datadir = '/home/egetzen/swp'
#vocab_file = '/home/egetzen/swp/vocab.txt'
#options_file = '/home/egetzen/swp/checkpoint/options.json'
#weight_file = '/home/egetzen/swp/swp_weights.hdf5'
batcher = Batcher(vocab_file, 50)
context_character_ids = tf.placeholder('int32', shape=(None, None, 50))
bilm = BidirectionalLanguageModel(options_file, weight_file)
context_embeddings_op = bilm(context_character_ids)
elmo_context_input = weight_layers('input', context_embeddings_op, l2_coef=0.0)

Instructions for updating:
Use the `axis` argument instead
USING SKIP CONNECTIONS


In [4]:
count = -1
for i in train_files:
    with open(i) as f:
        for s in f:
            count = count + 1
            diag.append(s.split("|")[0].split(",")) 

            
    

In [5]:
import itertools
flat_diag = list(itertools.chain(*diag))
events = np.unique(flat_diag)
events = np.ndarray.tolist(events)

In [7]:
passed = ['d_585']
names = ["Cardiac Dysrhythmia","Diabetes","Esophogeal Disease","Mitral Valve Disorder"]

In [6]:
count = -1
for i in train_files:
    with open(i) as f:
        for s in f:
            count = count + 1
            sentences.append(s.split("|")[2].split(" ") +
                             s.split("|")[3].replace("\n", "").split(" "))


In [9]:

print('fitting word2vec model')
model = gensim.models.Word2Vec(sentences, sg=skipgram, window=window,
                                                 iter=5, size=size, min_count=1, workers=20)



fitting word2vec model


In [10]:
AUC_logistic_word2vec = []
AUC_DL_word2vec = []
AUC_lasso_word2vec = []
F1_logistic_word2vec = []
F1_DL_word2vec = []
F1_lasso_word2vec = []
prevalence = []

for q in range(len(passed)):    
    list_duplicates = []
    next_diags = []
    final_dx_train = []
    prev_diags = []
    disease_prev = []
    count = -1
    for i in train_files:
        with open(i) as f:
            for s in f:
                count = count + 1
                next_diags = s.split("|")[0].split(",")
                final_dx_train.append(next_diags)
                prev_diags = [e for e in s.split("|")[2].split(" ") if e.startswith("d_")]

                if passed[q] in prev_diags: # if disease exit in the previous diagnosis
                    
                    disease_prev.append(1)
                    
                else:
                    disease_prev.append(0)


        # create a vector indicating which patients have disease as a final diagnosis
    disease_train = []
    for sublist in final_dx_train:
        if passed[q] in sublist:
            disease_train.append(1)
        else:
            disease_train.append(0)
    count = -1
    count2 = 0
    model.wv.init_sims()
    patient_seq_all_disease = []
    exclude = []
    for i in train_files: 
        with open(i) as f:
            for line in f:
                count = count + 1
                patient_seq = []
                feed_events = line.split("|")[2].split(" ")

                if disease_prev[count] == 1:
                    target = feed_events.index(passed[q])
                    feed_events = feed_events[:target]
                    if feed_events == []:
                        count2 = count2+1
                        exclude.append(1)
                    else:    
                        exclude.append(0)
                        te = len(feed_events)
                        weighted_events = [(e,  math.exp(decay*(j-te+1)/te)) for j, e in enumerate(feed_events) if e in model.wv.vocab]
                        sum_weights = sum(weight for event,weight in weighted_events)
                        for a in weighted_events:
                            event, weight = a
                            patient_seq.append(model.wv.word_vec(event,use_norm=norm))
                        patient_seq_all_disease.append(sum(patient_seq))

                else: 
                    exclude.append(0)
                    te = len(feed_events)
                    weighted_events = [(e,  math.exp(decay*(j-te+1)/te)) for j, e in enumerate(feed_events) if e in model.wv.vocab]
                    sum_weights = sum(weight for event,weight in weighted_events)
                    for a in weighted_events:
                        event, weight = a
                        patient_seq.append(model.wv.word_vec(event,use_norm=norm))
                    patient_seq_all_disease.append(sum(patient_seq))


    data_disease=pd.DataFrame(patient_seq_all_disease)


    a = 0
    disease_final = []
    for i in range(0,len(exclude)):
        if exclude[i] == 0:
            disease_final.append(disease_train[i])
        else:
            a = a+1


    data_disease[passed[q]] = disease_final


    X_train_disease=data_disease.iloc[:,0:100]
    Y_train_disease =data_disease.iloc[:,100]


    # create a vector with previous diagnoses and note when disease in previous diagnoses    
    dis_prev = []
    pt_count = 0
    demograph = []
    for i in valid_files: 
        with open(i) as f:
            for line in f:
                patient_seq_test = []
                prev_diags = [e for e in line.split("|")[2].split(" ") if e.startswith("d_")]
                next_diags = line.split("|")[0].split(",")
                demograph.append(line.split("|")[1].split(","))
                if passed[q] in prev_diags: # if disease exit in the previous diagnosis
                    
                    dis_prev.append(1)
                    
                else:
                    dis_prev.append(0)

   
    #create a vector of all final diagnoses
    final_dx_test = []
    for i in valid_files:
        with open(i) as f:
            for s in f:
                final_dx_test.append(s.split("|")[0].split(","))

    #create a vector when disease in final diagnoses
    count = -1
    disease_test = []
    for sublist in final_dx_test:
        count = count + 1
        if passed[q] in sublist:
            disease_test.append(1)
        else:
            disease_test.append(0)

    exclude=[]

    #create full testing dataset                
    count = -1
    count2 = 0
    model.wv.init_sims()
    patient_seq_all_disease_test = []
    exclude = []
    for i in valid_files: 
        with open(i) as f:
            for line in f:
                count = count + 1

                patient_seq = []
                feed_events = line.split("|")[2].split(" ")

                if dis_prev[count] == 1:
                    target = feed_events.index(passed[q])
                    feed_events = feed_events[:target]
                    if feed_events == []:
                        count2 = count2+1
                        exclude.append(1)
                    else:

                        exclude.append(0)
                        te = len(feed_events)
                        weighted_events = [(e,  math.exp(decay*(j-te+1)/te)) for j, e in enumerate(feed_events) if e in model.wv.vocab]
                        sum_weights = sum(weight for event,weight in weighted_events)
                        for a in weighted_events:
                            event, weight = a
                            patient_seq.append(model.wv.word_vec(event,use_norm=norm))
                        patient_seq_all_disease_test.append(sum(patient_seq))

                else:

                    exclude.append(0)
                    te = len(feed_events)
                    weighted_events = [(e,  math.exp(decay*(j-te+1)/te)) for j, e in enumerate(feed_events) if e in model.wv.vocab]
                    sum_weights = sum(weight for event,weight in weighted_events)
                    for a in weighted_events:
                        event, weight = a
                        patient_seq.append(model.wv.word_vec(event,use_norm=norm))
                    patient_seq_all_disease_test.append(sum(patient_seq))



 


    data_disease_test = pd.DataFrame(patient_seq_all_disease_test)

    disease_test_final = []
    for i in range(0,len(exclude)):
        if exclude[i] == 0:
            disease_test_final.append(disease_test[i])
        else:
            continue



    data_disease_test[passed[q]] = disease_test_final  
    X_disease_test=data_disease_test.iloc[:,0:100]
    Y_disease_test=data_disease_test.iloc[:,100]


    
    
    #lasso
    
    #Lasso
    
    searchCV_lasso = LogisticRegressionCV(Cs=list(np.power(10.0, np.arange(-10, 10))),penalty='l1',
    cv=5,random_state=777,fit_intercept=True,solver='liblinear',max_iter = 10000,scoring="f1")
    lasso_fit_disease = searchCV_lasso.fit(X_train_disease,Y_train_disease)
    print(lasso_fit_disease.C_)
    lasso_prob_disease = lasso_fit_disease.predict_proba(X_train_disease)[:,1]

    lasso_prob_disease = lasso_fit_disease.predict_proba(X_disease_test)[:,1]
    auc_disease_lasso = metrics.roc_auc_score(Y_disease_test, lasso_prob_disease)
    print('AUC disease Dys:,',auc_disease_lasso)
    print('Y_disease_test1 score:', f1_score(Y_disease_test, lasso_fit_disease.predict(X_disease_test)))

    
    
    
    
    y_pred_proba = lasso_prob_disease
    y_test = Y_disease_test

    fpr_wv_lasso, tpr_wv_lasso, _  = metrics.roc_curve(y_test,  y_pred_proba)
    auc_wv_lasso = metrics.roc_auc_score(y_test, y_pred_proba)
    
    #DL
    
    print("Reading files..."),
    tr_dataframe = data_disease
    te_dataframe = data_disease_test


    print("Finished\n")

    print("Compressing data..."),
    tr_X = tr_dataframe.iloc[:, :-1].values
    tr_Y = tr_dataframe.iloc[:, -1].values
    te_X = te_dataframe.iloc[:, :-1].values
    te_Y = te_dataframe.iloc[:, -1].values

    Max = tr_X.max(axis=0)
    Min = tr_X.min(axis=0)
    tr_scale_X = (tr_X - Min)/(Max - Min) * 0.8 + 0.1
    te_scale_X = (te_X - Min)/(Max - Min) * 0.8 + 0.1

    print("Finished\n")
    # In[6]:


    def baseline_model(units, act):
        model = Sequential()
        model.add(Dense(units, input_dim=len(tr_X[0]),activation=act))
        model.add(Dense(20,activation = act))
        model.add(Dense(1))

        model.compile(loss='mean_squared_error', optimizer='adam')
        return model



    # In[8]:

    from tensorflow.keras.callbacks import EarlyStopping
    print("Parameter optimization..."),


    seed = 7
    np.random.seed(seed)

    grid_list_units = range(50,60)
    grid_list_activation = ['relu','sigmoid']

    grid_dict = {'units':grid_list_units, 'act':grid_list_activation}
    grid_r2_score = make_scorer(r2_score, greater_is_better=True)
    grid_cv = KFold(n_splits=5, shuffle=True, random_state=seed)

    #earlystop = EarlyStopping(monitor='val_loss', patience=2, verbose=0, mode='auto')

    grid_DL = KerasRegressor(build_fn = baseline_model,batch_size = 300, nb_epoch=1000, verbose = 0)
    Grid = GridSearchCV(grid_DL, grid_dict, scoring=grid_r2_score, cv=grid_cv)
    Grid.fit(tr_scale_X,tr_Y)

    print("Fineshed\n")


    # In[31]:

    print("\nBest units=%f\nBest activaiton=%s" 
          %(Grid.best_params_['units'], Grid.best_params_['act']))


    # In[10]:

    from math import sqrt
    def model_valuation(y_true, y_pred):
        print("r=%.2f, mae=%.2f, mse=%.2f"
              % (sqrt(r2_score(y_true, y_pred)), mean_absolute_error(y_true, y_pred),
                 mean_squared_error(y_true, y_pred)))


    # model_DL = KerasRegressor(build_fn = baseline_model(units = Grid.best_params_['units'], act = Grid.best_params_['act']), nb_epoch=2000, batch_size=300,verbose = 0)

    model_DL = Sequential()
    model_DL.add(Dense(Grid.best_params_['units'], input_dim=len(tr_X[0]),activation=Grid.best_params_['act']))
    model_DL.add(Dense(20,activation = Grid.best_params_['act']))
    model_DL.add(Dense(1))
    model_DL.compile(loss='mean_squared_error', optimizer='adam')



    # In[ ]:




    # In[32]:


    model_DL.fit(tr_scale_X,tr_Y,batch_size = 300, nb_epoch=1000, verbose = 0)
    tr_predict_Y = model_DL.predict(tr_scale_X)
    te_predict_Y = model_DL.predict(te_scale_X)    


    

    yhat_classes = model_DL.predict_classes(te_scale_X, verbose=0)
    f1 = f1_score(te_Y, yhat_classes)
    print('F1 score: %f' % f1)

    # ROC AUC
    auc = metrics.roc_auc_score(te_Y, te_predict_Y)
    print('ROC AUC: %f' % auc)
    
    y_pred_proba = te_predict_Y
    y_test = te_Y

    fpr_wv_DL, tpr_wv_DL, _  = metrics.roc_curve(y_test,  y_pred_proba)
    auc_wv_DL = metrics.roc_auc_score(y_test, y_pred_proba)


[1000.]
AUC disease Dys:, 0.8739439861510634
Y_disease_test1 score: 0.6164154103852597
Reading files...
Finished

Compressing data...
Finished

Parameter optimization...
Fineshed


Best units=51.000000
Best activaiton=relu
F1 score: 0.602787
ROC AUC: 0.868532


In [11]:
patient_seq_all_disease_test

[array([-133.91943  ,  -83.79948  ,   53.425335 ,  249.311    ,
        -104.60275  , -182.48042  ,  122.68838  ,  232.48254  ,
           2.534884 ,  -94.86168  ,   94.35264  ,  151.33754  ,
         181.41348  ,  127.6039   ,  361.98016  ,  125.10052  ,
           1.5962915,   15.927731 , -151.72739  ,  131.7711   ,
          99.56435  ,  232.17465  ,  141.88834  ,   53.410126 ,
        -204.13814  ,   42.96992  ,  230.1913   ,  186.23087  ,
         -17.398024 ,  -34.91007  , -225.58923  , -148.38509  ,
         -65.7011   ,   41.863438 ,  144.41963  ,   33.057167 ,
         -13.611774 , -155.85112  , -210.42819  , -149.76372  ,
         140.88757  ,   11.415568 ,   63.85482  ,  -86.60396  ,
          75.01557  , -132.6711   ,   37.52247  ,  -74.17401  ,
        -187.13487  ,  167.23427  ,  -14.896246 ,   18.04482  ,
        -161.654    , -116.30531  ,  -51.39374  , -236.57089  ,
          -3.5851932,  -45.954796 , -132.64905  ,  245.85735  ,
         -13.586705 ,  -83.92237  ,   58

In [12]:
print('fitting fasttext model')
model = gensim.models.fasttext.FastText(sentences, sg=skipgram, window=window,
                                                 iter=5, size=size, min_count=1, workers=20)

fitting fasttext model


In [13]:
AUC_logistic_fasttext = []
AUC_DL_fasttext = []
F1_logistic_fasttext = []
F1_DL_fasttext = []
AUC_lasso_fasttext = []
F1_lasso_fasttext = []

for q in range(len(passed)):    
    list_duplicates = []
    next_diags = []
    final_dx_train = []
    prev_diags = []
    disease_prev = []
    count = -1
    for i in train_files:
        with open(i) as f:
            for s in f:
                count = count + 1
                next_diags = s.split("|")[0].split(",")
                final_dx_train.append(next_diags)
                prev_diags = [e for e in s.split("|")[2].split(" ") if e.startswith("d_")]

                if passed[q] in prev_diags: # if disease exit in the previous diagnosis
                    
                    disease_prev.append(1)
                    
                else:
                    disease_prev.append(0)


        # create a vector indicating which patients have disease as a final diagnosis
    disease_train = []
    for sublist in final_dx_train:
        if passed[q] in sublist:
            disease_train.append(1)
        else:
            disease_train.append(0)
    count = -1
    count2 = 0
    model.wv.init_sims()
    patient_seq_all_disease = []
    exclude = []
    for i in train_files: 
        with open(i) as f:
            for line in f:
                count = count + 1
                patient_seq = []
                feed_events = line.split("|")[2].split(" ")

                if disease_prev[count] == 1:
                    target = feed_events.index(passed[q])
                    feed_events = feed_events[:target]
                    if feed_events == []:
                        count2 = count2+1
                        exclude.append(1)
                    else:    
                        exclude.append(0)
                        te = len(feed_events)
                        weighted_events = [(e,  math.exp(decay*(j-te+1)/te)) for j, e in enumerate(feed_events) if e in model.wv.vocab]
                        sum_weights = sum(weight for event,weight in weighted_events)
                        for a in weighted_events:
                            event, weight = a
                            patient_seq.append(model.wv.word_vec(event,use_norm=norm))
                        patient_seq_all_disease.append(sum(patient_seq))

                else: 
                    exclude.append(0)
                    te = len(feed_events)
                    weighted_events = [(e,  math.exp(decay*(j-te+1)/te)) for j, e in enumerate(feed_events) if e in model.wv.vocab]
                    sum_weights = sum(weight for event,weight in weighted_events)
                    for a in weighted_events:
                        event, weight = a
                        patient_seq.append(model.wv.word_vec(event,use_norm=norm))
                    patient_seq_all_disease.append(sum(patient_seq))


    data_disease=pd.DataFrame(patient_seq_all_disease)


    a = 0
    disease_final = []
    for i in range(0,len(exclude)):
        if exclude[i] == 0:
            disease_final.append(disease_train[i])
        else:
            a = a+1


    data_disease[passed[q]] = disease_final


    X_train_disease=data_disease.iloc[:,0:100]
    Y_train_disease =data_disease.iloc[:,100]


    # create a vector with previous diagnoses and note when disease in previous diagnoses    
    dis_prev = []
    pt_count = 0
    demograph = []
    for i in valid_files: 
        with open(i) as f:
            for line in f:
                patient_seq_test = []
                prev_diags = [e for e in line.split("|")[2].split(" ") if e.startswith("d_")]
                next_diags = line.split("|")[0].split(",")
                demograph.append(line.split("|")[1].split(","))
                if passed[q] in prev_diags: # if disease exit in the previous diagnosis
                    
                    dis_prev.append(1)
                    
                else:
                    dis_prev.append(0)

   
    #create a vector of all final diagnoses
    final_dx_test = []
    for i in valid_files:
        with open(i) as f:
            for s in f:
                final_dx_test.append(s.split("|")[0].split(","))

    #create a vector when disease in final diagnoses
    count = -1
    disease_test = []
    for sublist in final_dx_test:
        count = count + 1
        if passed[q] in sublist:
            disease_test.append(1)
        else:
            disease_test.append(0)

    exclude=[]

    #create full testing dataset                
    count = -1
    count2 = 0
    model.wv.init_sims()
    patient_seq_all_disease_test = []
    exclude = []
    for i in valid_files: 
        with open(i) as f:
            for line in f:
                count = count + 1

                patient_seq = []
                feed_events = line.split("|")[2].split(" ")

                if dis_prev[count] == 1:
                    target = feed_events.index(passed[q])
                    feed_events = feed_events[:target]
                    if feed_events == []:
                        count2 = count2+1
                        exclude.append(1)
                    else:

                        exclude.append(0)
                        te = len(feed_events)
                        weighted_events = [(e,  math.exp(decay*(j-te+1)/te)) for j, e in enumerate(feed_events) if e in model.wv.vocab]
                        sum_weights = sum(weight for event,weight in weighted_events)
                        for a in weighted_events:
                            event, weight = a
                            patient_seq.append(model.wv.word_vec(event,use_norm=norm))
                        patient_seq_all_disease_test.append(sum(patient_seq))

                else:

                    exclude.append(0)
                    te = len(feed_events)
                    weighted_events = [(e,  math.exp(decay*(j-te+1)/te)) for j, e in enumerate(feed_events) if e in model.wv.vocab]
                    sum_weights = sum(weight for event,weight in weighted_events)
                    for a in weighted_events:
                        event, weight = a
                        patient_seq.append(model.wv.word_vec(event,use_norm=norm))
                    patient_seq_all_disease_test.append(sum(patient_seq))



 


    data_disease_test = pd.DataFrame(patient_seq_all_disease_test)

    disease_test_final = []
    for i in range(0,len(exclude)):
        if exclude[i] == 0:
            disease_test_final.append(disease_test[i])
        else:
            continue



    data_disease_test[passed[q]] = disease_test_final  
    X_disease_test=data_disease_test.iloc[:,0:100]
    Y_disease_test=data_disease_test.iloc[:,100]


   
    #Lasso
    
    searchCV_lasso = LogisticRegressionCV(Cs=list(np.power(10.0, np.arange(-10, 10))),penalty='l1',
    cv=5,random_state=777,fit_intercept=True,solver='liblinear',max_iter = 10000,scoring="f1")
    lasso_fit_disease = searchCV_lasso.fit(X_train_disease,Y_train_disease)
    print(lasso_fit_disease.C_)
    lasso_prob_disease = lasso_fit_disease.predict_proba(X_train_disease)[:,1]

    lasso_prob_disease = lasso_fit_disease.predict_proba(X_disease_test)[:,1]
    auc_disease_lasso = metrics.roc_auc_score(Y_disease_test, lasso_prob_disease)
    print('AUC disease Dys:,',auc_disease_lasso)
    print('Y_disease_test1 score:', f1_score(Y_disease_test, lasso_fit_disease.predict(X_disease_test)))


    y_pred_proba = lasso_prob_disease
    y_test = Y_disease_test

    fpr_ft_lasso, tpr_ft_lasso, _  = metrics.roc_curve(y_test,  y_pred_proba)
    auc_ft_lasso = metrics.roc_auc_score(y_test, y_pred_proba)
    
    print("Reading files..."),
    tr_dataframe = data_disease
    te_dataframe = data_disease_test


    print("Fineshed\n")

    print("Compressing data..."),
    tr_X = tr_dataframe.iloc[:, :-1].values
    tr_Y = tr_dataframe.iloc[:, -1].values
    te_X = te_dataframe.iloc[:, :-1].values
    te_Y = te_dataframe.iloc[:, -1].values

    Max = tr_X.max(axis=0)
    Min = tr_X.min(axis=0)
    tr_scale_X = (tr_X - Min)/(Max - Min) * 0.8 + 0.1
    te_scale_X = (te_X - Min)/(Max - Min) * 0.8 + 0.1

    print("Finished\n")
    # In[6]:


    def baseline_model(units, act):
        model = Sequential()
        model.add(Dense(units, input_dim=len(tr_X[0]),activation=act))
        model.add(Dense(20,activation = act))
        model.add(Dense(1))

        model.compile(loss='mean_squared_error', optimizer='adam')
        return model



    # In[8]:

    from tensorflow.keras.callbacks import EarlyStopping
    print("Parameter optimization..."),


    seed = 7
    np.random.seed(seed)

    grid_list_units = range(50,60)
    grid_list_activation = ['relu','sigmoid']

    grid_dict = {'units':grid_list_units, 'act':grid_list_activation}
    grid_r2_score = make_scorer(r2_score, greater_is_better=True)
    grid_cv = KFold(n_splits=5, shuffle=True, random_state=seed)

    #earlystop = EarlyStopping(monitor='val_loss', patience=2, verbose=0, mode='auto')

    grid_DL = KerasRegressor(build_fn = baseline_model,batch_size = 300, nb_epoch=1000, verbose = 0)
    Grid = GridSearchCV(grid_DL, grid_dict, scoring=grid_r2_score, cv=grid_cv)
    Grid.fit(tr_scale_X,tr_Y)

    print("Fineshed\n")


    # In[31]:

    print("\nBest units=%f\nBest activaiton=%s" 
          %(Grid.best_params_['units'], Grid.best_params_['act']))


    # In[10]:

    from math import sqrt
    def model_valuation(y_true, y_pred):
        print("r=%.2f, mae=%.2f, mse=%.2f"
              % (sqrt(r2_score(y_true, y_pred)), mean_absolute_error(y_true, y_pred),
                 mean_squared_error(y_true, y_pred)))


    # model_DL = KerasRegressor(build_fn = baseline_model(units = Grid.best_params_['units'], act = Grid.best_params_['act']), nb_epoch=2000, batch_size=300,verbose = 0)

    model_DL = Sequential()
    model_DL.add(Dense(Grid.best_params_['units'], input_dim=len(tr_X[0]),activation=Grid.best_params_['act']))
    model_DL.add(Dense(20,activation = Grid.best_params_['act']))
    model_DL.add(Dense(1))
    model_DL.compile(loss='mean_squared_error', optimizer='adam')



    # In[ ]:




    # In[32]:


    model_DL.fit(tr_scale_X,tr_Y,batch_size = 300, nb_epoch=1000, verbose = 0)
    tr_predict_Y = model_DL.predict(tr_scale_X)
    te_predict_Y = model_DL.predict(te_scale_X)    


   

    yhat_classes = model_DL.predict_classes(te_scale_X, verbose=0)
    f1 = f1_score(te_Y, yhat_classes)
    print('F1 score: %f' % f1)

    # ROC AUC
    auc = metrics.roc_auc_score(te_Y, te_predict_Y)
    print('ROC AUC: %f' % auc)
    
    y_pred_proba = te_predict_Y
    y_test = te_Y

    fpr_ft_DL, tpr_ft_DL, _  = metrics.roc_curve(y_test,  y_pred_proba)
    auc_ft_DL = metrics.roc_auc_score(y_test, y_pred_proba)


[1.]
AUC disease Dys:, 0.8708275431320469
Y_disease_test1 score: 0.5779334500875657
Reading files...
Fineshed

Compressing data...
Finished

Parameter optimization...
Fineshed


Best units=55.000000
Best activaiton=sigmoid
F1 score: 0.320542
ROC AUC: 0.850015


In [14]:
print('fitting glove model')
corpus = Corpus()
corpus.fit(sentences, window = 10)
glove = Glove(no_components = 100, learning_rate = 0.05)
glove.fit(corpus.matrix, epochs=70,no_threads=4,verbose=True)
glove.add_dictionary(corpus.dictionary)
glove.save('glove.model')

fitting glove model
Performing 70 training epochs with 4 threads
Epoch 0
Epoch 1
Epoch 2
Epoch 3
Epoch 4
Epoch 5
Epoch 6
Epoch 7
Epoch 8
Epoch 9
Epoch 10
Epoch 11
Epoch 12
Epoch 13
Epoch 14
Epoch 15
Epoch 16
Epoch 17
Epoch 18
Epoch 19
Epoch 20
Epoch 21
Epoch 22
Epoch 23
Epoch 24
Epoch 25
Epoch 26
Epoch 27
Epoch 28
Epoch 29
Epoch 30
Epoch 31
Epoch 32
Epoch 33
Epoch 34
Epoch 35
Epoch 36
Epoch 37
Epoch 38
Epoch 39
Epoch 40
Epoch 41
Epoch 42
Epoch 43
Epoch 44
Epoch 45
Epoch 46
Epoch 47
Epoch 48
Epoch 49
Epoch 50
Epoch 51
Epoch 52
Epoch 53
Epoch 54
Epoch 55
Epoch 56
Epoch 57
Epoch 58
Epoch 59
Epoch 60
Epoch 61
Epoch 62
Epoch 63
Epoch 64
Epoch 65
Epoch 66
Epoch 67
Epoch 68
Epoch 69


In [15]:
AUC_logistic_glove = []
AUC_DL_glove = []
F1_logistic_glove = []
F1_DL_glove = []
AUC_lasso_glove = []
F1_lasso_glove = []


for q in range(len(passed)):    
    list_duplicates = []
    next_diags = []
    final_dx_train = []
    prev_diags = []
    disease_prev = []
    count = -1
    for i in train_files:
        with open(i) as f:
            for s in f:
                count = count + 1
                next_diags = s.split("|")[0].split(",")
                final_dx_train.append(next_diags)
                prev_diags = [e for e in s.split("|")[2].split(" ") if e.startswith("d_")]

                if passed[q] in prev_diags: # if disease exit in the previous diagnosis
                    
                    disease_prev.append(1)
                    
                else:
                    disease_prev.append(0)


        # create a vector indicating which patients have disease as a final diagnosis
    disease_train = []
    for sublist in final_dx_train:
        if passed[q] in sublist:
            disease_train.append(1)
        else:
            disease_train.append(0)
    count = -1
    count2 = 0
    
    patient_seq_all_disease = []
    exclude = []
    for i in train_files: 
        with open(i) as f:
            for line in f:
                count = count + 1
                patient_seq = []
                feed_events = line.split("|")[2].split(" ")

                if disease_prev[count] == 1:
                    target = feed_events.index(passed[q])
                    feed_events = feed_events[:target]
                    if feed_events == []:
                        count2 = count2+1
                        exclude.append(1)
                    else:    
                        exclude.append(0)
                        te = len(feed_events)
                        weighted_events = [(e,  math.exp(decay*(j-te+1)/te)) for j, e in enumerate(feed_events) if e in glove.dictionary]
                        sum_weights = sum(weight for event,weight in weighted_events)
                        for a in weighted_events:
                            event, weight = a
                            patient_seq.append(glove.word_vectors[glove.dictionary[event]])
                        patient_seq_all_disease.append(sum(patient_seq))

                else: 
                    exclude.append(0)
                    te = len(feed_events)
                    weighted_events = [(e,  math.exp(decay*(j-te+1)/te)) for j, e in enumerate(feed_events) if e in glove.dictionary]
                    sum_weights = sum(weight for event,weight in weighted_events)
                    for a in weighted_events:
                        event, weight = a
                        patient_seq.append(glove.word_vectors[glove.dictionary[event]])
                    patient_seq_all_disease.append(sum(patient_seq))


    data_disease=pd.DataFrame(patient_seq_all_disease)


    a = 0
    disease_final = []
    for i in range(0,len(exclude)):
        if exclude[i] == 0:
            disease_final.append(disease_train[i])
        else:
            a = a+1


    data_disease[passed[q]] = disease_final


    X_train_disease=data_disease.iloc[:,0:100]
    Y_train_disease =data_disease.iloc[:,100]



   

    # create a vector with previous diagnoses and note when disease in previous diagnoses    
    dis_prev = []
    pt_count = 0
    demograph = []
    for i in valid_files: 
        with open(i) as f:
            for line in f:
                patient_seq_test = []
                prev_diags = [e for e in line.split("|")[2].split(" ") if e.startswith("d_")]
                next_diags = line.split("|")[0].split(",")
                demograph.append(line.split("|")[1].split(","))
                if passed[q] in prev_diags: # if disease exit in the previous diagnosis
                    
                    dis_prev.append(1)
                    
                else:
                    dis_prev.append(0)
   
    #create a vector of all final diagnoses
    final_dx_test = []
    for i in valid_files:
        with open(i) as f:
            for s in f:
                final_dx_test.append(s.split("|")[0].split(","))

    #create a vector when disease in final diagnoses
    count = -1
    disease_test = []
    for sublist in final_dx_test:
        count = count + 1
        if passed[q] in sublist:
            disease_test.append(1)
        else:
            disease_test.append(0)

    exclude=[]

    #create full testing dataset                
    count = -1
    count2 = 0
    
    patient_seq_all_disease_test = []
    exclude = []
    for i in valid_files: 
        with open(i) as f:
            for line in f:
                count = count + 1

                patient_seq = []
                feed_events = line.split("|")[2].split(" ")

                if dis_prev[count] == 1:
                    target = feed_events.index(passed[q])
                    feed_events = feed_events[:target]
                    if feed_events == []:
                        count2 = count2+1
                        exclude.append(1)
                    else:

                        exclude.append(0)
                        te = len(feed_events)
                        weighted_events = [(e,  math.exp(decay*(j-te+1)/te)) for j, e in enumerate(feed_events) if e in glove.dictionary]
                        sum_weights = sum(weight for event,weight in weighted_events)
                        for a in weighted_events:
                            event, weight = a
                            patient_seq.append(glove.word_vectors[glove.dictionary[event]])
                        patient_seq_all_disease_test.append(sum(patient_seq))

                else:

                    exclude.append(0)
                    te = len(feed_events)
                    weighted_events = [(e,  math.exp(decay*(j-te+1)/te)) for j, e in enumerate(feed_events) if e in glove.dictionary]
                    sum_weights = sum(weight for event,weight in weighted_events)
                    for a in weighted_events:
                        event, weight = a
                        patient_seq.append(glove.word_vectors[glove.dictionary[event]])
                    patient_seq_all_disease_test.append(sum(patient_seq))



 


    data_disease_test = pd.DataFrame(patient_seq_all_disease_test)

    disease_test_final = []
    for i in range(0,len(exclude)):
        if exclude[i] == 0:
            disease_test_final.append(disease_test[i])
        else:
            continue



    data_disease_test[passed[q]] = disease_test_final  
    X_disease_test=data_disease_test.iloc[:,0:100]
    Y_disease_test=data_disease_test.iloc[:,100]


    

    #Lasso
    
    searchCV_lasso = LogisticRegressionCV(Cs=list(np.power(10.0, np.arange(-10, 10))),penalty='l1',
    cv=5,random_state=777,fit_intercept=True,solver='liblinear',max_iter = 10000,scoring="f1")
    lasso_fit_disease = searchCV_lasso.fit(X_train_disease,Y_train_disease)
    print(lasso_fit_disease.C_)
    lasso_prob_disease = lasso_fit_disease.predict_proba(X_train_disease)[:,1]

    lasso_prob_disease = lasso_fit_disease.predict_proba(X_disease_test)[:,1]
    auc_disease_lasso = metrics.roc_auc_score(Y_disease_test, lasso_prob_disease)
    print('AUC disease Dys:,',auc_disease_lasso)
    print('Y_disease_test1 score:', f1_score(Y_disease_test, lasso_fit_disease.predict(X_disease_test)))


    y_pred_proba = lasso_prob_disease
    y_test = Y_disease_test

    fpr_glove_lasso, tpr_glove_lasso, _  = metrics.roc_curve(y_test,  y_pred_proba)
    auc_glove_lasso = metrics.roc_auc_score(y_test, y_pred_proba)



    print("Reading files..."),
    tr_dataframe = data_disease
    te_dataframe = data_disease_test


    print("Fineshed\n")

    print("Compressing data..."),
    tr_X = tr_dataframe.iloc[:, :-1].values
    tr_Y = tr_dataframe.iloc[:, -1].values
    te_X = te_dataframe.iloc[:, :-1].values
    te_Y = te_dataframe.iloc[:, -1].values

    Max = tr_X.max(axis=0)
    Min = tr_X.min(axis=0)
    tr_scale_X = (tr_X - Min)/(Max - Min) * 0.8 + 0.1
    te_scale_X = (te_X - Min)/(Max - Min) * 0.8 + 0.1

    print("Finished\n")
    # In[6]:


    def baseline_model(units, act):
        model = Sequential()
        model.add(Dense(units, input_dim=len(tr_X[0]),activation=act))
        model.add(Dense(20,activation = act))
        model.add(Dense(1))

        model.compile(loss='mean_squared_error', optimizer='adam')
        return model



    # In[8]:

    from tensorflow.keras.callbacks import EarlyStopping
    print("Parameter optimization..."),


    seed = 7
    np.random.seed(seed)

    grid_list_units = range(50,60)
    grid_list_activation = ['relu','sigmoid']

    grid_dict = {'units':grid_list_units, 'act':grid_list_activation}
    grid_r2_score = make_scorer(r2_score, greater_is_better=True)
    grid_cv = KFold(n_splits=5, shuffle=True, random_state=seed)

    #earlystop = EarlyStopping(monitor='val_loss', patience=2, verbose=0, mode='auto')

    grid_DL = KerasRegressor(build_fn = baseline_model,batch_size = 300, nb_epoch=1000, verbose = 0)
    Grid = GridSearchCV(grid_DL, grid_dict, scoring=grid_r2_score, cv=grid_cv)
    Grid.fit(tr_scale_X,tr_Y)

    print("Fineshed\n")


    # In[31]:

    print("\nBest units=%f\nBest activaiton=%s" 
          %(Grid.best_params_['units'], Grid.best_params_['act']))


    # In[10]:

    from math import sqrt
    def model_valuation(y_true, y_pred):
        print("r=%.2f, mae=%.2f, mse=%.2f"
              % (sqrt(r2_score(y_true, y_pred)), mean_absolute_error(y_true, y_pred),
                 mean_squared_error(y_true, y_pred)))


    # model_DL = KerasRegressor(build_fn = baseline_model(units = Grid.best_params_['units'], act = Grid.best_params_['act']), nb_epoch=2000, batch_size=300,verbose = 0)

    model_DL = Sequential()
    model_DL.add(Dense(Grid.best_params_['units'], input_dim=len(tr_X[0]),activation=Grid.best_params_['act']))
    model_DL.add(Dense(20,activation = Grid.best_params_['act']))
    model_DL.add(Dense(1))
    model_DL.compile(loss='mean_squared_error', optimizer='adam')



    # In[ ]:




    # In[32]:


    model_DL.fit(tr_scale_X,tr_Y,batch_size = 300, nb_epoch=1000, verbose = 0)
    tr_predict_Y = model_DL.predict(tr_scale_X)
    te_predict_Y = model_DL.predict(te_scale_X)    




    yhat_classes = model_DL.predict_classes(te_scale_X, verbose=0)
    f1 = f1_score(te_Y, yhat_classes)
    print('F1 score: %f' % f1)

    # ROC AUC
    auc = metrics.roc_auc_score(te_Y, te_predict_Y)
    print('ROC AUC: %f' % auc)
    
    y_pred_proba = te_predict_Y
    y_test = te_Y

    fpr_glove_DL, tpr_glove_DL, _  = metrics.roc_curve(y_test,  y_pred_proba)
    auc_glove_DL = metrics.roc_auc_score(y_test, y_pred_proba)


[1.]
AUC disease Dys:, 0.860185819535905
Y_disease_test1 score: 0.5758620689655172
Reading files...
Fineshed

Compressing data...
Finished

Parameter optimization...
Fineshed


Best units=53.000000
Best activaiton=relu
F1 score: 0.611382
ROC AUC: 0.858504


In [15]:
count = -1
for i in train_files:
    with open(i) as f:
        for s in f:
            count = count + 1
            sentences.append(s.split("|")[2].split(" ") +
                             s.split("|")[3].replace("\n", "").split(" "))
import itertools

flat_sentences = list(itertools.chain(*sentences))
count = 0
events = np.unique(flat_sentences)
events = np.ndarray.tolist(events)

sentenzes=[]
for n in range(len(sentences)):
    sentz = []
    for i in range(len(sentences[n])):
        sentz.append(sentences[n][i].replace("_",r""))
    sentenzes.append(sentz)

sentences = []
for n in range(len(sentenzes)):
    sentz = []
    for i in range(len(sentenzes[n])):
        sentz.append(sentenzes[n][i].replace(".",r""))
    sentences.append(sentz)

pls = []
for n in range(len(sentences)):
    sentz = []
    for i in range(len(sentences[n])):
        sentz.append(sentences[n][i].replace("/",r"q"))
    pls.append(sentz)

import itertools
sentences = pls
flat_sentences = list(itertools.chain(*sentences))
count = 0
events = np.unique(flat_sentences)
events = np.ndarray.tolist(events)


events = np.unique(flat_sentences)
events = np.ndarray.tolist(events)
bert_dict = []
for i in range(len(events)):
    bert_dict.append(bc.encode([events[i]]))
    
bertdict = []
for i in range(len(bert_dict)):
    bert = np.array(bert_dict[i])
    bertdict.append(bert.flatten())
bert_dict = bertdict

In [16]:
bert_dict

[array([-3.73863518e-01, -7.84543097e-01, -4.59551215e-01,  2.04664707e+00,
         2.42034006e+00, -1.96673346e+00,  2.26281881e-01,  3.36709559e-01,
        -3.67969990e-01, -8.08525085e-01,  4.38517779e-01,  2.68536305e+00,
        -1.02285981e+00,  8.26191008e-01,  1.04644549e+00, -5.25692105e-01,
         3.73513162e-01, -1.28285974e-01,  2.88167894e-01,  4.91368204e-01,
         3.72087091e-01, -4.85125810e-01, -1.37598801e+00, -6.48969114e-01,
         3.39879513e-01, -2.23445272e+00,  1.18028879e+00,  4.01944481e-02,
        -1.52447790e-01,  9.22656059e-01,  6.73486829e-01, -9.82726097e-01,
        -6.86573505e-01,  3.48281175e-01, -9.48341072e-01,  1.60483408e+00,
        -7.62659192e-01, -1.91369668e-01, -1.14151394e+00, -7.59664595e-01,
         1.42970547e-01, -5.82337201e-01, -6.86141104e-02,  1.28984556e-01,
        -1.59799367e-01, -1.89769328e+00,  7.31189609e-01, -1.06142104e+00,
        -5.60786307e-01,  1.67161119e+00,  6.62356257e-01,  1.10034585e+00,
         9.9

In [10]:
embeddings = pd.read_excel('/Users/emily/Documents/bert_embeddings.xlsx')
events_df = pd.read_excel('/Users/emily/Documents/events.xlsx')
events = events_df.iloc[:,1].to_list()

In [14]:
len(np.array(embeddings.iloc[events.index('d_250'),1:101]))

100

In [ ]:
AUC_logistic_bert = []
AUC_DL_bert = []
F1_logistic_bert = []
F1_DL_bert = []
AUC_lasso_bert = []
F1_lasso_bert = []

for q in range(len(passed)):    
    list_duplicates = []
    next_diags = []
    final_dx_train = []
    prev_diags = []
    disease_prev = []
    count = -1
    for i in train_files:
        with open(i) as f:
            for s in f:
                count = count + 1
                next_diags = s.split("|")[0].split(",")
                final_dx_train.append(next_diags)
                prev_diags = [e for e in s.split("|")[2].split(" ") if e.startswith("d_")]

                if passed[q] in prev_diags: # if disease exit in the previous diagnosis
                    
                    disease_prev.append(1)
                    
                else:
                    disease_prev.append(0)


        # create a vector indicating which patients have disease as a final diagnosis
    disease_train = []
    for sublist in final_dx_train:
        if passed[q] in sublist:
            disease_train.append(1)
        else:
            disease_train.append(0)
    count = -1
    count2 = 0

    patient_seq_all_disease = []
    exclude = []
    for i in train_files: 
        with open(i) as f:
            for line in f:
                count = count + 1
                patient_seq = []
                feed_events = line.split("|")[2].split(" ")

                if disease_prev[count] == 1:
                    target = feed_events.index(passed[q])
                    feed_events = feed_events[:target]
                    if feed_events == []:
                        count2 = count2+1
                        exclude.append(1)
                    else:    
                        exclude.append(0)
                        te = len(feed_events)
                        weighted_events = [(e,  math.exp(decay*(j-te+1)/te)) for j, e in enumerate(feed_events) if e in events]
                        sum_weights = sum(weight for event,weight in weighted_events)
                        for a in weighted_events:
                            event, weight = a
                            patient_seq.append(bert_dict[events.index(event)])
                        patient_seq_all_disease.append(sum(patient_seq))

                else: 
                    exclude.append(0)
                    te = len(feed_events)
                    weighted_events = [(e,  math.exp(decay*(j-te+1)/te)) for j, e in enumerate(feed_events) if e in events]
                    sum_weights = sum(weight for event,weight in weighted_events)
                    for a in weighted_events:
                        event, weight = a
                        patient_seq.append(bert_dict[events.index(event)])
                    patient_seq_all_disease.append(sum(patient_seq))


    data_disease=pd.DataFrame(patient_seq_all_disease)


    a = 0
    disease_final = []
    for i in range(0,len(exclude)):
        if exclude[i] == 0:
            disease_final.append(disease_train[i])
        else:
            a = a+1


    data_disease[passed[q]] = disease_final


    X_train_disease=data_disease.iloc[:,0:100]
    Y_train_disease =data_disease.iloc[:,100]



   

    # create a vector with previous diagnoses and note when disease in previous diagnoses    
    dis_prev = []
    pt_count = 0
    demograph = []
    for i in valid_files: 
        with open(i) as f:
            for line in f:
                patient_seq_test = []
                prev_diags = [e for e in line.split("|")[2].split(" ") if e.startswith("d_")]
                next_diags = line.split("|")[0].split(",")
                demograph.append(line.split("|")[1].split(","))
                if passed[q] in prev_diags: # if disease exit in the previous diagnosis
                    
                    dis_prev.append(1)
                    
                else:
                    dis_prev.append(0)

   
    #create a vector of all final diagnoses
    final_dx_test = []
    for i in valid_files:
        with open(i) as f:
            for s in f:
                final_dx_test.append(s.split("|")[0].split(","))

    #create a vector when disease in final diagnoses
    count = -1
    disease_test = []
    for sublist in final_dx_test:
        count = count + 1
        if passed[q] in sublist:
            disease_test.append(1)
        else:
            disease_test.append(0)

    exclude=[]

    #create full testing dataset                
    count = -1
    count2 = 0
  
    patient_seq_all_disease_test = []
    exclude = []
    for i in valid_files: 
        with open(i) as f:
            for line in f:
                count = count + 1

                patient_seq = []
                feed_events = line.split("|")[2].split(" ")

                if dis_prev[count] == 1:
                    target = feed_events.index(passed[q])
                    feed_events = feed_events[:target]
                    if feed_events == []:
                        count2 = count2+1
                        exclude.append(1)
                    else:

                        exclude.append(0)
                        te = len(feed_events)
                        weighted_events = [(e,  math.exp(decay*(j-te+1)/te)) for j, e in enumerate(feed_events) if e in events]
                        sum_weights = sum(weight for event,weight in weighted_events)
                        for a in weighted_events:
                            event, weight = a
                            patient_seq.append(bert_dict[events.index(event)])
                        patient_seq_all_disease_test.append(sum(patient_seq))

                else:

                    exclude.append(0)
                    te = len(feed_events)
                    weighted_events = [(e,  math.exp(decay*(j-te+1)/te)) for j, e in enumerate(feed_events) if e in events]
                    sum_weights = sum(weight for event,weight in weighted_events)
                    for a in weighted_events:
                        event, weight = a
                        patient_seq.append(bert_dict[events.index(event)])
                    patient_seq_all_disease_test.append(sum(patient_seq))



 


    data_disease_test = pd.DataFrame(patient_seq_all_disease_test)

    disease_test_final = []
    for i in range(0,len(exclude)):
        if exclude[i] == 0:
            disease_test_final.append(disease_test[i])
        else:
            continue



    data_disease_test[passed[q]] = disease_test_final  
    X_disease_test=data_disease_test.iloc[:,0:100]
    Y_disease_test=data_disease_test.iloc[:,100]


    
    #Lasso
    
    searchCV_lasso = LogisticRegressionCV(Cs=list(np.power(10.0, np.arange(-10, 10))),penalty='l1',
    cv=5,random_state=777,fit_intercept=True,solver='liblinear',max_iter = 10000,scoring="f1")
    lasso_fit_disease = searchCV_lasso.fit(X_train_disease,Y_train_disease)
    print(lasso_fit_disease.C_)
    lasso_prob_disease = lasso_fit_disease.predict_proba(X_train_disease)[:,1]

    lasso_prob_disease = lasso_fit_disease.predict_proba(X_disease_test)[:,1]
    auc_disease_lasso = metrics.roc_auc_score(Y_disease_test, lasso_prob_disease)
    print('AUC disease Dys:,',auc_disease_lasso)
    print('Y_disease_test1 score:', f1_score(Y_disease_test, lasso_fit_disease.predict(X_disease_test)))


    y_pred_proba = lasso_prob_disease
    y_test = Y_disease_test

    fpr_bert_lasso, tpr_bert_lasso, _  = metrics.roc_curve(y_test,  y_pred_proba)
    auc_bert_lasso = metrics.roc_auc_score(y_test, y_pred_proba)


    print("Reading files..."),
    tr_dataframe = data_disease
    te_dataframe = data_disease_test


    print("Fineshed\n")

    print("Compressing data..."),
    tr_X = tr_dataframe.iloc[:, :-1].values
    tr_Y = tr_dataframe.iloc[:, -1].values
    te_X = te_dataframe.iloc[:, :-1].values
    te_Y = te_dataframe.iloc[:, -1].values

    Max = tr_X.max(axis=0)
    Min = tr_X.min(axis=0)
    tr_scale_X = (tr_X - Min)/(Max - Min) * 0.8 + 0.1
    te_scale_X = (te_X - Min)/(Max - Min) * 0.8 + 0.1

    print("Finished\n")
    # In[6]:


    def baseline_model(units, act):
        model = Sequential()
        model.add(Dense(units, input_dim=len(tr_X[0]),activation=act))
        model.add(Dense(20,activation = act))
        model.add(Dense(1))

        model.compile(loss='mean_squared_error', optimizer='adam')
        return model



    # In[8]:

    from tensorflow.keras.callbacks import EarlyStopping
    print("Parameter optimization..."),


    seed = 7
    np.random.seed(seed)

    grid_list_units = range(50,60)
    grid_list_activation = ['relu','sigmoid']

    grid_dict = {'units':grid_list_units, 'act':grid_list_activation}
    grid_r2_score = make_scorer(r2_score, greater_is_better=True)
    grid_cv = KFold(n_splits=5, shuffle=True, random_state=seed)

    #earlystop = EarlyStopping(monitor='val_loss', patience=2, verbose=0, mode='auto')

    grid_DL = KerasRegressor(build_fn = baseline_model,batch_size = 300, nb_epoch=1000, verbose = 0)
    Grid = GridSearchCV(grid_DL, grid_dict, scoring=grid_r2_score, cv=grid_cv)
    Grid.fit(tr_scale_X,tr_Y)

    print("Fineshed\n")


    # In[31]:

    print("\nBest units=%f\nBest activaiton=%s" 
          %(Grid.best_params_['units'], Grid.best_params_['act']))


    # In[10]:

    from math import sqrt
    def model_valuation(y_true, y_pred):
        print("r=%.2f, mae=%.2f, mse=%.2f"
              % (sqrt(r2_score(y_true, y_pred)), mean_absolute_error(y_true, y_pred),
                 mean_squared_error(y_true, y_pred)))


    # model_DL = KerasRegressor(build_fn = baseline_model(units = Grid.best_params_['units'], act = Grid.best_params_['act']), nb_epoch=2000, batch_size=300,verbose = 0)

    model_DL = Sequential()
    model_DL.add(Dense(Grid.best_params_['units'], input_dim=len(tr_X[0]),activation=Grid.best_params_['act']))
    model_DL.add(Dense(20,activation = Grid.best_params_['act']))
    model_DL.add(Dense(1))
    model_DL.compile(loss='mean_squared_error', optimizer='adam')



    # In[ ]:




    # In[32]:


    model_DL.fit(tr_scale_X,tr_Y,batch_size = 300, nb_epoch=1000, verbose = 0)
    tr_predict_Y = model_DL.predict(tr_scale_X)
    te_predict_Y = model_DL.predict(te_scale_X)    


    

    yhat_classes = model_DL.predict_classes(te_scale_X, verbose=0)
    f1 = f1_score(te_Y, yhat_classes)
    print('F1 score: %f' % f1)

    # ROC AUC
    auc = metrics.roc_auc_score(te_Y, te_predict_Y)
    print('ROC AUC: %f' % auc)
    
    y_pred_proba = te_predict_Y
    y_test = te_Y

    fpr_bert_DL, tpr_bert_DL, _  = metrics.roc_curve(y_test,  y_pred_proba)
    auc_bert_DL = metrics.roc_auc_score(y_test, y_pred_proba)

[1000.]
AUC disease Dys:, 0.8530906167401833
Y_disease_test1 score: 0.498069498069498
Reading files...
Fineshed

Compressing data...
Finished

Parameter optimization...


In [ ]:
embeddings = pd.read_excel('/Users/emily/Documents/elmoembeddings.xlsx')
events_df = pd.read_excel('/Users/emily/Documents/events.xlsx')
events = events_df.iloc[:,1].to_list()

In [ ]:
AUC_logistic_elmo = []
AUC_DL_elmo = []
F1_logistic_elmo = []
F1_DL_elmo = []
AUC_lasso_elmo = []
F1_lasso_elmo = []

for q in range(len(passed)):    
    list_duplicates = []
    next_diags = []
    final_dx_train = []
    prev_diags = []
    disease_prev = []
    count = -1
    for i in train_files:
        with open(i) as f:
            for s in f:
                count = count + 1
                next_diags = s.split("|")[0].split(",")
                final_dx_train.append(next_diags)
                prev_diags = [e for e in s.split("|")[2].split(" ") if e.startswith("d_")]

                if passed[q] in prev_diags: # if disease exit in the previous diagnosis
                    
                    disease_prev.append(1)
                    
                else:
                    disease_prev.append(0)


        # create a vector indicating which patients have disease as a final diagnosis
    disease_train = []
    for sublist in final_dx_train:
        if passed[q] in sublist:
            disease_train.append(1)
        else:
            disease_train.append(0)
    count = -1
    count2 = 0
    
    patient_seq_all_disease = []
    exclude = []
    for i in train_files: 
        with open(i) as f:
            for line in f:
                count = count + 1
                patient_seq = []
                feed_events = line.split("|")[2].split(" ")

                if disease_prev[count] == 1:
                    target = feed_events.index(passed[q])
                    feed_events = feed_events[:target]
                    if feed_events == []:
                        count2 = count2+1
                        exclude.append(1)
                    else:    
                        exclude.append(0)
                        te = len(feed_events)
                        weighted_events = [(e,  math.exp(decay*(j-te+1)/te)) for j, e in enumerate(feed_events) if e in events]
                        sum_weights = sum(weight for event,weight in weighted_events)
                        for a in weighted_events:
                            event, weight = a
                            patient_seq.append(np.array(embeddings.iloc[events.index(event),1:-1]))
                        patient_seq_all_disease.append(sum(patient_seq))

                else: 
                    exclude.append(0)
                    te = len(feed_events)
                    weighted_events = [(e,  math.exp(decay*(j-te+1)/te)) for j, e in enumerate(feed_events) if e in events]
                    sum_weights = sum(weight for event,weight in weighted_events)
                    for a in weighted_events:
                        event, weight = a
                        patient_seq.append(np.array(embeddings.iloc[events.index(event),1:-1]))
                    patient_seq_all_disease.append(sum(patient_seq))


    data_disease=pd.DataFrame(patient_seq_all_disease)


    a = 0
    disease_final = []
    for i in range(0,len(exclude)):
        if exclude[i] == 0:
            disease_final.append(disease_train[i])
        else:
            a = a+1


    data_disease[passed[q]] = disease_final


    X_train_disease=data_disease.iloc[:,0:100]
    Y_train_disease =data_disease.iloc[:,100]



   
    # create a vector with previous diagnoses and note when disease in previous diagnoses    
    dis_prev = []
    pt_count = 0
    demograph = []
    for i in valid_files: 
        with open(i) as f:
            for line in f:
                patient_seq_test = []
                prev_diags = [e for e in line.split("|")[2].split(" ") if e.startswith("d_")]
                next_diags = line.split("|")[0].split(",")
                demograph.append(line.split("|")[1].split(","))
                if passed[q] in prev_diags: # if disease exit in the previous diagnosis
                    
                    dis_prev.append(1)
                    
                else:
                    dis_prev.append(0)

   
    #create a vector of all final diagnoses
    final_dx_test = []
    for i in valid_files:
        with open(i) as f:
            for s in f:
                final_dx_test.append(s.split("|")[0].split(","))

    #create a vector when disease in final diagnoses
    count = -1
    disease_test = []
    for sublist in final_dx_test:
        count = count + 1
        if passed[q] in sublist:
            disease_test.append(1)
        else:
            disease_test.append(0)

    exclude=[]

    #create full testing dataset                
    count = -1
    count2 = 0
   
    patient_seq_all_disease_test = []
    exclude = []
    for i in valid_files: 
        with open(i) as f:
            for line in f:
                count = count + 1

                patient_seq = []
                feed_events = line.split("|")[2].split(" ")

                if dis_prev[count] == 1:
                    target = feed_events.index(passed[q])
                    feed_events = feed_events[:target]
                    if feed_events == []:
                        count2 = count2+1
                        exclude.append(1)
                    else:

                        exclude.append(0)
                        te = len(feed_events)
                        weighted_events = [(e,  math.exp(decay*(j-te+1)/te)) for j, e in enumerate(feed_events) if e in events]
                        sum_weights = sum(weight for event,weight in weighted_events)
                        for a in weighted_events:
                            event, weight = a
                            patient_seq.append(np.array(embeddings.iloc[events.index(event),1:-1]))
                        patient_seq_all_disease_test.append(sum(patient_seq))

                else:

                    exclude.append(0)
                    te = len(feed_events)
                    weighted_events = [(e,  math.exp(decay*(j-te+1)/te)) for j, e in enumerate(feed_events) if e in events]
                    sum_weights = sum(weight for event,weight in weighted_events)
                    for a in weighted_events:
                        event, weight = a
                        patient_seq.append(np.array(embeddings.iloc[events.index(event),1:-1]))
                    patient_seq_all_disease_test.append(sum(patient_seq))



 


    data_disease_test = pd.DataFrame(patient_seq_all_disease_test)

    disease_test_final = []
    for i in range(0,len(exclude)):
        if exclude[i] == 0:
            disease_test_final.append(disease_test[i])
        else:
            continue



    data_disease_test[passed[q]] = disease_test_final  
    X_disease_test=data_disease_test.iloc[:,0:100]
    Y_disease_test=data_disease_test.iloc[:,100]


   
    #Lasso
    
    searchCV_lasso = LogisticRegressionCV(Cs=list(np.power(10.0, np.arange(-10, 10))),penalty='l1',
    cv=5,random_state=777,fit_intercept=True,solver='liblinear',max_iter = 10000,scoring="f1")
    lasso_fit_disease = searchCV_lasso.fit(X_train_disease,Y_train_disease)
    print(lasso_fit_disease.C_)
    lasso_prob_disease = lasso_fit_disease.predict_proba(X_train_disease)[:,1]

    lasso_prob_disease = lasso_fit_disease.predict_proba(X_disease_test)[:,1]
    auc_disease_lasso = metrics.roc_auc_score(Y_disease_test, lasso_prob_disease)
    print('AUC disease Dys:,',auc_disease_lasso)
    print('Y_disease_test1 score:', f1_score(Y_disease_test, lasso_fit_disease.predict(X_disease_test)))

    y_pred_proba = lasso_prob_disease
    y_test = Y_disease_test

    fpr_elmo_lasso, tpr_elmo_lasso, _  = metrics.roc_curve(y_test,  y_pred_proba)
    auc_elmo_lasso = metrics.roc_auc_score(y_test, y_pred_proba)
    
    print("Reading files..."),
    tr_dataframe = data_disease
    te_dataframe = data_disease_test


    print("Fineshed\n")

    print("Compressing data..."),
    tr_X = tr_dataframe.iloc[:, :-1].values
    tr_Y = tr_dataframe.iloc[:, -1].values
    te_X = te_dataframe.iloc[:, :-1].values
    te_Y = te_dataframe.iloc[:, -1].values

    Max = tr_X.max(axis=0)
    Min = tr_X.min(axis=0)
    tr_scale_X = (tr_X - Min)/(Max - Min) * 0.8 + 0.1
    te_scale_X = (te_X - Min)/(Max - Min) * 0.8 + 0.1

    print("Finished\n")
    # In[6]:


    def baseline_model(units, act):
        model = Sequential()
        model.add(Dense(units, input_dim=len(tr_X[0]),activation=act))
        model.add(Dense(20,activation = act))
        model.add(Dense(1))

        model.compile(loss='mean_squared_error', optimizer='adam')
        return model



    # In[8]:

    from tensorflow.keras.callbacks import EarlyStopping
    print("Parameter optimization..."),


    seed = 7
    np.random.seed(seed)

    grid_list_units = range(50,60)
    grid_list_activation = ['relu','sigmoid']

    grid_dict = {'units':grid_list_units, 'act':grid_list_activation}
    grid_r2_score = make_scorer(r2_score, greater_is_better=True)
    grid_cv = KFold(n_splits=5, shuffle=True, random_state=seed)

    #earlystop = EarlyStopping(monitor='val_loss', patience=2, verbose=0, mode='auto')

    grid_DL = KerasRegressor(build_fn = baseline_model,batch_size = 300, nb_epoch=1000, verbose = 0)
    Grid = GridSearchCV(grid_DL, grid_dict, scoring=grid_r2_score, cv=grid_cv)
    Grid.fit(tr_scale_X,tr_Y)

    print("Fineshed\n")


    # In[31]:

    print("\nBest units=%f\nBest activaiton=%s" 
          %(Grid.best_params_['units'], Grid.best_params_['act']))


    # In[10]:

    from math import sqrt
    def model_valuation(y_true, y_pred):
        print("r=%.2f, mae=%.2f, mse=%.2f"
              % (sqrt(r2_score(y_true, y_pred)), mean_absolute_error(y_true, y_pred),
                 mean_squared_error(y_true, y_pred)))


    # model_DL = KerasRegressor(build_fn = baseline_model(units = Grid.best_params_['units'], act = Grid.best_params_['act']), nb_epoch=2000, batch_size=300,verbose = 0)

    model_DL = Sequential()
    model_DL.add(Dense(Grid.best_params_['units'], input_dim=len(tr_X[0]),activation=Grid.best_params_['act']))
    model_DL.add(Dense(20,activation = Grid.best_params_['act']))
    model_DL.add(Dense(1))
    model_DL.compile(loss='mean_squared_error', optimizer='adam')



    # In[ ]:




    # In[32]:


    model_DL.fit(tr_scale_X,tr_Y,batch_size = 300, nb_epoch=1000, verbose = 0)
    tr_predict_Y = model_DL.predict(tr_scale_X)
    te_predict_Y = model_DL.predict(te_scale_X)    


   
    yhat_classes = model_DL.predict_classes(te_scale_X, verbose=0)
    f1 = f1_score(te_Y, yhat_classes)
    print('F1 score: %f' % f1)

    # ROC AUC
    auc = metrics.roc_auc_score(te_Y, te_predict_Y)
    print('ROC AUC: %f' % auc)
    
    y_pred_proba = te_predict_Y
    y_test = te_Y

    fpr_elmo_DL, tpr_elmo_DL, _  = metrics.roc_curve(y_test,  y_pred_proba)
    auc_elmo_DL = metrics.roc_auc_score(y_test, y_pred_proba)
    


In [ ]:
weight*np.array(embeddings.iloc[events.index(event),1:-1]

In [ ]:
patient_seq.append(weight*np.array(embeddings.iloc[events.index(event),1:-1]))


In [ ]:
import matplotlib.pyplot as plt

randx = [0.0,0.2,0.4,0.6,0.8,1.0]
randy = [0.0,0.2,0.4,0.6,0.8,1.0]

plt.plot(fpr_wv_lasso,tpr_wv_lasso,'blue',label="Word2Vec, auc=0.9242")
plt.plot(fpr_ft_lasso,tpr_ft_lasso,'red',label="FastText, auc=0.9246")
plt.plot(fpr_glove_lasso,tpr_glove_lasso,'green',label="GloVe, auc=0.9271")
plt.plot(fpr_bert_lasso,tpr_bert_lasso,'purple',label="BERT, auc=0.9149")
plt.plot(fpr_elmo_lasso,tpr_elmo_lasso,'orange',label="ELMo, auc=0.9207")
plt.plot(randx,randy,color = 'black',linestyle = 'dashed',label = 'random classifier')
plt.xlabel('False Positive Rate')
plt.ylabel('True Positive Rate')
plt.title('ROC Curve (lasso) Diabetes')
plt.legend(loc='upper center', bbox_to_anchor=(.81, .5), shadow=True, ncol=1)
plt.savefig('/users/emily/Documents/plots/lasso_cardiac')

In [ ]:
len(fpr_glove_lasso)

In [ ]:
randx = [0.0,0.2,0.4,0.6,0.8,1.0]
randy = [0.0,0.2,0.4,0.6,0.8,1.0]

plt.plot(fpr_wv_DL,tpr_wv_DL,'blue',label="Word2Vec, auc=0.9356")
plt.plot(fpr_ft_DL,tpr_ft_DL,'red',label="FastText, auc=0.9353")
plt.plot(fpr_glove_DL,tpr_glove_DL,'green',label="GloVe, auc=0.9248")
plt.plot(fpr_bert_DL,tpr_bert_DL,'purple',label="BERT, auc=0.9248")
plt.plot(fpr_elmo_DL,tpr_elmo_DL,'orange',label="ELMo, auc=0.9281")
plt.plot(randx,randy,color = 'black',linestyle = 'dashed',label = 'random classifier')
plt.xlabel('False Positive Rate')
plt.ylabel('True Positive Rate') 
plt.title('ROC Curve (DL) Diabetes')
plt.legend(loc='upper center', bbox_to_anchor=(.81, .5), shadow=True, ncol=1)
plt.savefig('/users/emily/Documents/plots/DL_cardiac')

In [ ]:
s